In [1]:
import json
import nltk
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
from nltk.corpus import stopwords
import random
import numpy as np
import pickle
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, Dropout
from tensorflow.keras.optimizers import SGD
from tensorflow.keras.models import load_model

In [2]:
data_file = open('intents.json', encoding = 'utf8').read()

In [3]:
intents = json.loads(data_file)

In [24]:
words = []
classes = []
documents = []
ignore_words = ['?', '!', '(', ')','.', ',']

In [25]:
for intent in intents['intents']:
    print(intent['tag'])

greeting
goodbye
thanks
noanswer
stem_borer
rice_hispa
brown_planthopper
gall_midge
whorl_maggot
case_worm
leaf_roller
swarming_caterpillar
long_horned_cricket
grass_hopper
green_semilooper
green_leaf_hopper
zigzag_leaf_hopper
thrips
white_backed_plant_hopper
mealy_bug
rice_bug
army_worm
long_horned_cricket
rat
bacterial_leaf_blight
bacterial_leaf_streak
foot_rot
blast
sheath_blight
false_smut
brown_spot
stem_rot
sheath_rot
leaf_scald
narrow_brown_leaf_spot
tungro
ufra
bakanae


In [26]:
for intent in intents['intents']:
    for pattern in intent['patterns']:
        w = nltk.word_tokenize(pattern)
        words.extend(w)
        documents.append((w, intent['tag']))
    if intent['tag'] not in classes:
        classes.append(intent['tag'])

In [27]:
words

['Hi',
 'there',
 'How',
 'are',
 'you',
 'how',
 'r',
 'you',
 'how',
 'are',
 'u',
 'Is',
 'anyone',
 'there',
 '?',
 'Hey',
 'Hola',
 'Hello',
 'Good',
 'day',
 'Bye',
 'See',
 'you',
 'later',
 'Goodbye',
 'Nice',
 'chatting',
 'to',
 'you',
 ',',
 'bye',
 'Till',
 'next',
 'time',
 'Thanks',
 'Thank',
 'you',
 'That',
 "'s",
 'helpful',
 'Awesome',
 ',',
 'thanks',
 'Thanks',
 'for',
 'helping',
 'me',
 'majra',
 'insects',
 'mejra',
 'insects',
 'white',
 'rice',
 'mazra',
 'insects',
 'white',
 'panicles',
 'on',
 'the',
 'rice',
 'Mazra',
 'moths',
 'seeing',
 'so',
 'many',
 'mazra',
 'moths',
 '.',
 'what',
 'to',
 'do',
 '?',
 'stem',
 'borer',
 'stem_borer',
 'yellow',
 'stem',
 'borer',
 'How',
 'to',
 'control',
 'rice',
 'yellow',
 'stem',
 'borer',
 '?',
 'Ways',
 'to',
 'control',
 'stem',
 'borer',
 'in',
 'rice',
 'Seeing',
 'Deadhearts',
 ',',
 'Dead',
 'tillers',
 'in',
 'rice',
 'plant',
 '.',
 'What',
 'to',
 'do',
 '?',
 'Deadhearts',
 'or',
 'Dead',
 'tillers',

In [28]:
documents

[(['Hi', 'there'], 'greeting'),
 (['How', 'are', 'you'], 'greeting'),
 (['how', 'r', 'you'], 'greeting'),
 (['how', 'are', 'u'], 'greeting'),
 (['Is', 'anyone', 'there', '?'], 'greeting'),
 (['Hey'], 'greeting'),
 (['Hola'], 'greeting'),
 (['Hello'], 'greeting'),
 (['Good', 'day'], 'greeting'),
 (['Bye'], 'goodbye'),
 (['See', 'you', 'later'], 'goodbye'),
 (['Goodbye'], 'goodbye'),
 (['Nice', 'chatting', 'to', 'you', ',', 'bye'], 'goodbye'),
 (['Till', 'next', 'time'], 'goodbye'),
 (['Thanks'], 'thanks'),
 (['Thank', 'you'], 'thanks'),
 (['That', "'s", 'helpful'], 'thanks'),
 (['Awesome', ',', 'thanks'], 'thanks'),
 (['Thanks', 'for', 'helping', 'me'], 'thanks'),
 ([], 'noanswer'),
 (['majra', 'insects'], 'stem_borer'),
 (['mejra', 'insects'], 'stem_borer'),
 (['white', 'rice'], 'stem_borer'),
 (['mazra', 'insects'], 'stem_borer'),
 (['white', 'panicles', 'on', 'the', 'rice'], 'stem_borer'),
 (['Mazra', 'moths'], 'stem_borer'),
 (['seeing', 'so', 'many', 'mazra', 'moths', '.', 'what', 

In [29]:
classes

['greeting',
 'goodbye',
 'thanks',
 'noanswer',
 'stem_borer',
 'rice_hispa',
 'brown_planthopper',
 'gall_midge',
 'whorl_maggot',
 'case_worm',
 'leaf_roller',
 'swarming_caterpillar',
 'long_horned_cricket',
 'grass_hopper',
 'green_semilooper',
 'green_leaf_hopper',
 'zigzag_leaf_hopper',
 'thrips',
 'white_backed_plant_hopper',
 'mealy_bug',
 'rice_bug',
 'army_worm',
 'rat',
 'bacterial_leaf_blight',
 'bacterial_leaf_streak',
 'foot_rot',
 'blast',
 'sheath_blight',
 'false_smut',
 'brown_spot',
 'stem_rot',
 'sheath_rot',
 'leaf_scald',
 'narrow_brown_leaf_spot',
 'tungro',
 'ufra',
 'bakanae']

In [30]:
words = [word for word in words if word.isalpha()]
stop_words = set(stopwords.words('english'))
words = [w for w in words if not w in stop_words]
words = [lemmatizer.lemmatize(w.lower(), pos = 'v') for w in words if w not in ignore_words]
words = [word for word in words if len(word)>1]

In [31]:
words

['hi',
 'how',
 'be',
 'anyone',
 'hey',
 'hola',
 'hello',
 'good',
 'day',
 'bye',
 'see',
 'later',
 'goodbye',
 'nice',
 'chat',
 'bye',
 'till',
 'next',
 'time',
 'thank',
 'thank',
 'that',
 'helpful',
 'awesome',
 'thank',
 'thank',
 'help',
 'majra',
 'insects',
 'mejra',
 'insects',
 'white',
 'rice',
 'mazra',
 'insects',
 'white',
 'panicles',
 'rice',
 'mazra',
 'moths',
 'see',
 'many',
 'mazra',
 'moths',
 'stem',
 'borer',
 'yellow',
 'stem',
 'borer',
 'how',
 'control',
 'rice',
 'yellow',
 'stem',
 'borer',
 'ways',
 'control',
 'stem',
 'borer',
 'rice',
 'see',
 'deadhearts',
 'dead',
 'tiller',
 'rice',
 'plant',
 'what',
 'deadhearts',
 'dead',
 'tiller',
 'easily',
 'pull',
 'base',
 'whiteheads',
 'reproductive',
 'stage',
 'emerge',
 'panicles',
 'whitish',
 'unfilled',
 'empty',
 'white',
 'head',
 'white',
 'head',
 'rice',
 'see',
 'whiteheads',
 'rice',
 'plant',
 'tiny',
 'hole',
 'stem',
 'tiller',
 'see',
 'tiny',
 'hole',
 'stem',
 'see',
 'tiny',
 'ho

In [32]:
words = sorted(list(set(words)))

In [33]:
classes = sorted(list(set(classes)))

In [34]:
words

['abnormal',
 'absorb',
 'abundant',
 'accord',
 'accumulate',
 'across',
 'addition',
 'adult',
 'adults',
 'advice',
 'affect',
 'after',
 'agar',
 'age',
 'air',
 'all',
 'almost',
 'along',
 'alpin',
 'also',
 'alternate',
 'aman',
 'and',
 'angle',
 'another',
 'anyone',
 'apex',
 'appear',
 'appearance',
 'area',
 'areas',
 'army',
 'armyworm',
 'armyworms',
 'around',
 'arrival',
 'as',
 'ash',
 'at',
 'attach',
 'attack',
 'away',
 'awesome',
 'back',
 'bacteria',
 'bacterial',
 'bakanae',
 'bakni',
 'ball',
 'basal',
 'base',
 'be',
 'bead',
 'bear',
 'bearers',
 'become',
 'beet',
 'before',
 'begin',
 'belly',
 'belong',
 'bend',
 'bhuyajhul',
 'big',
 'bigger',
 'bite',
 'black',
 'blade',
 'blades',
 'blast',
 'blend',
 'blight',
 'blotch',
 'bluish',
 'body',
 'border',
 'borer',
 'bottom',
 'boundaries',
 'branch',
 'break',
 'bright',
 'brittle',
 'broad',
 'brown',
 'brownish',
 'bud',
 'bug',
 'bunch',
 'burn',
 'but',
 'bye',
 'call',
 'can',
 'carrier',
 'carry',
 '

In [41]:
classes

['army_worm',
 'bacterial_leaf_blight',
 'bacterial_leaf_streak',
 'bakanae',
 'blast',
 'brown_planthopper',
 'brown_spot',
 'case_worm',
 'false_smut',
 'foot_rot',
 'gall_midge',
 'goodbye',
 'grass_hopper',
 'green_leaf_hopper',
 'green_semilooper',
 'greeting',
 'leaf_roller',
 'leaf_scald',
 'long_horned_cricket',
 'mealy_bug',
 'narrow_brown_leaf_spot',
 'noanswer',
 'rat',
 'rice_bug',
 'rice_hispa',
 'sheath_blight',
 'sheath_rot',
 'stem_borer',
 'stem_rot',
 'swarming_caterpillar',
 'thanks',
 'thrips',
 'tungro',
 'ufra',
 'white_backed_plant_hopper',
 'whorl_maggot',
 'zigzag_leaf_hopper']

In [42]:
print(len(documents), "documents")

492 documents


In [43]:
print(len(classes), "classes", classes)

37 classes ['army_worm', 'bacterial_leaf_blight', 'bacterial_leaf_streak', 'bakanae', 'blast', 'brown_planthopper', 'brown_spot', 'case_worm', 'false_smut', 'foot_rot', 'gall_midge', 'goodbye', 'grass_hopper', 'green_leaf_hopper', 'green_semilooper', 'greeting', 'leaf_roller', 'leaf_scald', 'long_horned_cricket', 'mealy_bug', 'narrow_brown_leaf_spot', 'noanswer', 'rat', 'rice_bug', 'rice_hispa', 'sheath_blight', 'sheath_rot', 'stem_borer', 'stem_rot', 'swarming_caterpillar', 'thanks', 'thrips', 'tungro', 'ufra', 'white_backed_plant_hopper', 'whorl_maggot', 'zigzag_leaf_hopper']


In [44]:
print(len(words), "Unique Lemmatized words", words)

924 Unique Lemmatized words ["'s", '.oblong', '.on', '1', '2-3', 'a', 'abnormal', 'about', 'above', 'absorb', 'abundant', 'accord', 'accumulate', 'across', 'addition', 'adult', 'adults', 'advice', 'affect', 'after', 'against', 'agar', 'age', 'air', 'akran-', 'all', 'almost', 'along', 'alpin', 'also', 'alternate', 'aman', 'an', 'and', 'angle', 'another', 'any', 'anyone', 'apex', 'appear', 'appearance', 'area', 'areas', 'army', 'armyworm', 'armyworms', 'around', 'arrival', 'as', 'ash', 'at', 'attach', 'attack', 'attack-prone', 'away', 'awesome', 'back', 'bacteria', 'bacterial', 'bakanae', 'bakni', 'ball', 'basal', 'base', 'be', 'bead', 'bear', 'bearers', 'because', 'become', 'beet', 'before', 'begin', 'belly', 'belong', 'bend', 'between', 'bhuyajhul', 'big', 'bigger', 'bite', 'black', 'blade', 'blades', 'blast', 'blend', 'blight', 'blotch', 'bluish', 'body', 'border', 'borer', 'both', 'bottom', 'boundaries', 'branch', 'break', 'bright', 'brittle', 'broad', 'brown', 'brown-green', 'browni

In [45]:
training = []
output_empty = [0] * len(classes)
len(output_empty)

37

In [46]:
output_empty

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0]

In [47]:
for doc in documents:
    bag = []
    pattern_words = doc[0]
    print(doc)
    print(doc[0])

(['Hi', 'there'], 'greeting')
['Hi', 'there']
(['How', 'are', 'you'], 'greeting')
['How', 'are', 'you']
(['how', 'r', 'you'], 'greeting')
['how', 'r', 'you']
(['how', 'are', 'u'], 'greeting')
['how', 'are', 'u']
(['Is', 'anyone', 'there', '?'], 'greeting')
['Is', 'anyone', 'there', '?']
(['Hey'], 'greeting')
['Hey']
(['Hola'], 'greeting')
['Hola']
(['Hello'], 'greeting')
['Hello']
(['Good', 'day'], 'greeting')
['Good', 'day']
(['Bye'], 'goodbye')
['Bye']
(['See', 'you', 'later'], 'goodbye')
['See', 'you', 'later']
(['Goodbye'], 'goodbye')
['Goodbye']
(['Nice', 'chatting', 'to', 'you', ',', 'bye'], 'goodbye')
['Nice', 'chatting', 'to', 'you', ',', 'bye']
(['Till', 'next', 'time'], 'goodbye')
['Till', 'next', 'time']
(['Thanks'], 'thanks')
['Thanks']
(['Thank', 'you'], 'thanks')
['Thank', 'you']
(['That', "'s", 'helpful'], 'thanks')
['That', "'s", 'helpful']
(['Awesome', ',', 'thanks'], 'thanks')
['Awesome', ',', 'thanks']
(['Thanks', 'for', 'helping', 'me'], 'thanks')
['Thanks', 'for', 

In [48]:
for doc in documents:
    bag = []
    pattern_words = doc[0]
    pattern_words = [lemmatizer.lemmatize(word.lower(), pos = 'v') for word in pattern_words]
    for w in words:
        bag.append(1) if w in pattern_words else bag.append(0)
    output_row = list(output_empty)
    output_row[classes.index(doc[1])] = 1
    training.append([bag, output_row])

In [49]:
print(bag)

[0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

In [50]:
print(training)

[[[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

In [51]:
random.shuffle(training)

In [52]:
training = np.array(training, dtype = object)

In [53]:
print(training)

[[list([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [54]:
print(len(training))

492


In [55]:
train_x = list(training[:,0])

In [56]:
train_y = list(training[:,1])

In [57]:
print(train_x)

[[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [58]:
print(train_y)

[[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

In [59]:
print(train_x[0], " ", train_y[0])

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

In [60]:
model = Sequential()
model.add(Dense(128, input_shape = (len(train_x[0]), ), activation = 'relu'))
model.add(Dropout(0.5))
model.add(Dense(64, activation = 'relu'))
model.add(Dropout(0.5))
model.add(Dense(len(train_y[0]), activation = 'softmax'))

In [61]:
sgd = SGD(lr = 0.01, decay = 1e-6, momentum = 0.9, nesterov = True)
model.compile(loss = 'categorical_crossentropy', optimizer = sgd, metrics = ['accuracy'])

In [62]:
hist = model.fit(np.array(train_x), np.array(train_y), epochs = 600, batch_size = 5, verbose = 1)

Epoch 1/600
99/99 [==============================] - 0s 1ms/step - loss: 3.5779 - accuracy: 0.0569
Epoch 2/600
99/99 [==============================] - 0s 1ms/step - loss: 3.4237 - accuracy: 0.0854
Epoch 3/600
99/99 [==============================] - 0s 1ms/step - loss: 3.2213 - accuracy: 0.1362
Epoch 4/600
99/99 [==============================] - 0s 1ms/step - loss: 3.0605 - accuracy: 0.1789
Epoch 5/600
99/99 [==============================] - 0s 1ms/step - loss: 2.7469 - accuracy: 0.2622
Epoch 6/600
99/99 [==============================] - 0s 1ms/step - loss: 2.5795 - accuracy: 0.2907
Epoch 7/600
99/99 [==============================] - 0s 1ms/step - loss: 2.3303 - accuracy: 0.3659
Epoch 8/600
99/99 [==============================] - 0s 1ms/step - loss: 2.2087 - accuracy: 0.3618
Epoch 9/600
99/99 [==============================] - 0s 1ms/step - loss: 1.9630 - accuracy: 0.4350
Epoch 10/600
99/99 [==============================] - 0s 1ms/step - loss: 1.8291 - accuracy: 0.4675
Epoch 11/

99/99 [==============================] - 0s 1ms/step - loss: 0.8168 - accuracy: 0.7988
Epoch 84/600
99/99 [==============================] - 0s 2ms/step - loss: 1.0323 - accuracy: 0.7988
Epoch 85/600
99/99 [==============================] - 0s 1ms/step - loss: 0.8677 - accuracy: 0.8028
Epoch 86/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6006 - accuracy: 0.8354
Epoch 87/600
99/99 [==============================] - 0s 1ms/step - loss: 0.5590 - accuracy: 0.8435
Epoch 88/600
99/99 [==============================] - 0s 1ms/step - loss: 0.7917 - accuracy: 0.8150
Epoch 89/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6361 - accuracy: 0.8374
Epoch 90/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6906 - accuracy: 0.8577
Epoch 91/600
99/99 [==============================] - 0s 1ms/step - loss: 0.4851 - accuracy: 0.8679
Epoch 92/600
99/99 [==============================] - 0s 1ms/step - loss: 0.8583 - accuracy: 0.8191
Epoch 93/600


99/99 [==============================] - 0s 1ms/step - loss: 0.7790 - accuracy: 0.8272
Epoch 245/600
99/99 [==============================] - 0s 1ms/step - loss: 0.7579 - accuracy: 0.8130
Epoch 246/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6882 - accuracy: 0.8150
Epoch 247/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6760 - accuracy: 0.8272
Epoch 248/600
99/99 [==============================] - 0s 1ms/step - loss: 0.7419 - accuracy: 0.8110
Epoch 249/600
99/99 [==============================] - 0s 2ms/step - loss: 0.7544 - accuracy: 0.8415
Epoch 250/600
99/99 [==============================] - 0s 1ms/step - loss: 0.9186 - accuracy: 0.8191
Epoch 251/600
99/99 [==============================] - 0s 1ms/step - loss: 0.7375 - accuracy: 0.8252
Epoch 252/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6543 - accuracy: 0.8313
Epoch 253/600
99/99 [==============================] - 0s 1ms/step - loss: 0.8604 - accuracy: 0.8110
Epoc

99/99 [==============================] - 0s 1ms/step - loss: 0.6904 - accuracy: 0.8028
Epoch 406/600
99/99 [==============================] - 0s 1ms/step - loss: 0.5911 - accuracy: 0.8476
Epoch 407/600
99/99 [==============================] - 0s 1ms/step - loss: 0.7097 - accuracy: 0.8618
Epoch 408/600
99/99 [==============================] - 0s 1ms/step - loss: 0.8097 - accuracy: 0.8171
Epoch 409/600
99/99 [==============================] - 0s 1ms/step - loss: 0.7735 - accuracy: 0.8171
Epoch 410/600
99/99 [==============================] - 0s 1ms/step - loss: 0.5639 - accuracy: 0.8455
Epoch 411/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6672 - accuracy: 0.8232
Epoch 412/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6281 - accuracy: 0.8211
Epoch 413/600
99/99 [==============================] - 0s 1ms/step - loss: 0.7035 - accuracy: 0.8171
Epoch 414/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6183 - accuracy: 0.8191
Epoc

99/99 [==============================] - 0s 1ms/step - loss: 0.6576 - accuracy: 0.8150
Epoch 568/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6639 - accuracy: 0.8191
Epoch 569/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6405 - accuracy: 0.8171
Epoch 570/600
99/99 [==============================] - 0s 1ms/step - loss: 0.7264 - accuracy: 0.8191
Epoch 571/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6891 - accuracy: 0.8150
Epoch 572/600
99/99 [==============================] - 0s 1ms/step - loss: 0.8038 - accuracy: 0.8171
Epoch 573/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6267 - accuracy: 0.8272
Epoch 574/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6427 - accuracy: 0.8150
Epoch 575/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6524 - accuracy: 0.8435
Epoch 576/600
99/99 [==============================] - 0s 1ms/step - loss: 0.6583 - accuracy: 0.8211
Epoc

In [63]:
model.save('model.h5', hist)

In [15]:
model = load_model('model.h5')

In [16]:
intents = json.loads(open('intents.json', encoding = 'utf8').read())

In [17]:
words = pickle.load(open("words.pkl", "rb"))

In [18]:
classes = pickle.load(open("labels.pkl", "rb"))

In [19]:
def clean_up_sentence(sentence):
    sentence_words = nltk.word_tokenize(sentence)
    sentence_words = [lemmatizer.lemmatize(word.lower(), pos = 'v') for word in sentence_words]
    return sentence_words

In [20]:
sentence = clean_up_sentence("Here we going again some direction")
sentence

['here', 'we', 'go', 'again', 'some', 'direction']

In [21]:
def bow(sentence, words, show_details = True):
    sentence_words = clean_up_sentence(sentence)
    bag = [0]* len(words)
    for s in sentence_words:
        for i,w in enumerate(words):
            if w == s:
                bag[i] = 1
    return (np.array(bag))

In [22]:
def predict_class(sentence, model):
    p = bow(sentence, words, show_details = False)
    res = model.predict(np.array([p]))[0]
    print(res)
    ERROR_THRESHOLD = 0.1
    results = [[i,r] for i,r in enumerate(res) if r > ERROR_THRESHOLD]
    results.sort(key = lambda x: x[1], reverse = True)
    print(results)
    return_list = []
    for r in results:
        return_list.append({"intent" : classes[r[0]], "Probability" : str(r[1])})
    for i in return_list:
        print(i)
    return return_list
    

In [23]:
def getResponse(ints, intents_json):
    list_of_intents = intents_json['intents']
    print(len(ints))
    if len(ints) == 0:
        for i in list_of_intents:
            if(i['tag'] == 'noanswer'):
                return random.choice(i['responses'])
    tag = ints[0]['intent']
    print(tag)
    for i in list_of_intents:
        if (i['tag'] == tag):
            result = random.choice(i['responses'])
            break
    return result

In [24]:
def chatbot_response(text):
    ints = predict_class(text, model)
    res = getResponse(ints, intents)
    return res

In [25]:
y = chatbot_response("rice plants are short, leaves are yellow")
y

[2.4758310e-03 5.0068682e-04 1.7362020e-03 9.7095156e-03 7.5585307e-03
 3.2232683e-02 4.3312614e-03 1.6767150e-02 2.2973262e-03 1.1680635e-02
 9.1843180e-02 1.6021576e-02 2.2526795e-02 1.2802023e-01 1.0686714e-02
 1.4001511e-02 1.2973877e-02 3.6359055e-03 9.9839701e-04 3.8914052e-01
 2.6723577e-03 3.0082393e-02 3.7216704e-04 7.9581356e-03 7.9782866e-03
 3.3592428e-03 1.6177259e-02 2.9562974e-02 1.2333201e-02 4.8309471e-03
 1.2012708e-02 9.0069715e-03 1.4931847e-02 4.7129309e-03 4.2769019e-02
 1.8217457e-02 3.8834175e-03]
[[19, 0.38914052], [13, 0.12802023]]
{'intent': 'mealy_bug', 'Probability': '0.38914052'}
{'intent': 'green_leaf_hopper', 'Probability': '0.12802023'}
2
mealy_bug


'If the infestation is severe, spray Phenitrothion insecticide (such as Sumithion or Folithion 20 ml per 10 liters of water) 2-3 times in 10 days'